## SDK code to create CUSTOMER_X_PRODUCT_product_ProductGroup_Representation_in_CUSTOMER_item_TotalCost_14d

Feature description:
>The feature assesses the representation of a given product_ProductGroup in a given CUSTOMER's item TotalCost over a 14d period. A value greater than 1 indicates this product_ProductGroup is over-represented for the particular customer. The evaluation is done by comparing: 
 - the Percentage of a customer's total item TotalCost, that match the ProductGroup of a specific product over a 14d period. 
 - the Percentage of the total item TotalCost, that match the ProductGroup of a specific product over a 14d period.

In [ ]:
import featurebyte as fb
fb.use_profile("tutorial")

### Activate catalog

 See [SDK reference for catalogs](https://docs.featurebyte.com/latest/reference/core/catalog/)

In [ ]:
catalog = fb.Catalog.activate("Grocery Dataset Tutorial")

### Set windows for aggregation

In [ ]:
windows = ['14d']

### Get view from table
 See [SDK reference for views](https://docs.featurebyte.com/latest/reference/core/view/)

In [ ]:
# Get view from GROCERYPRODUCT dimension table.
groceryproduct_view = catalog.get_view("GROCERYPRODUCT")

In [ ]:
# Get view from INVOICEITEMS item table.
invoiceitems_view = catalog.get_view("INVOICEITEMS")

### Join views
 See [SDK reference for views](https://docs.featurebyte.com/latest/reference/core/view/)

In [ ]:
# Join GROCERYPRODUCT view to INVOICEITEMS view.
invoiceitems_view = invoiceitems_view.join(groceryproduct_view, rsuffix="")

### Create Lookup feature
 See [SDK reference for features](https://docs.featurebyte.com/latest/reference/core/feature/)

 See [SDK reference to declare a lookup feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.ViewColumn.as_feature/)

In [ ]:
# Create lookup feature from ProductGroup column for product entity.
product_productgroup =\
groceryproduct_view["ProductGroup"].as_feature("PRODUCT_ProductGroup")

### Do window aggregation from INVOICEITEMS
 See [SDK reference for features](https://docs.featurebyte.com/latest/reference/core/feature/)

 See [SDK reference to groupby a view](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.GroupByMixin.groupby/)

 See [SDK reference to do aggregation over time](https://docs.featurebyte.com/latest/reference/featurebyte.api.groupby.GroupBy.aggregate_over/)

 See [SDK reference for feature group](https://docs.featurebyte.com/latest/reference/core/feature_group/)

 See [list of aggregation operations](https://docs.featurebyte.com/latest/reference/featurebyte.enum.AggFunc/)

In [ ]:
# Group INVOICEITEMS view by customer entity (GroceryCustomerGuid) across different ProductGroups.
invoiceitems_view_by_customer_across_productgroup =\
invoiceitems_view.groupby(
    ['GroceryCustomerGuid'], category="ProductGroup"
)

In [ ]:
# Distribution representing the cumulative TotalCost of item, categorized by their respective
# product's ProductGroup, for the customer over time.
feature_group =\
invoiceitems_view_by_customer_across_productgroup.aggregate_over(
    "TotalCost", method=fb.AggFunc.SUM,
    feature_names=[
        "CUSTOMER_item_TotalCost_across_product_ProductGroups"
        + "_" + w for w in windows
    ],
    windows=windows
)
# Get CUSTOMER_item_TotalCost_across_product_ProductGroups_14d object from feature group.
customer_item_totalcost_across_product_productgroups_14d =\
feature_group["CUSTOMER_item_TotalCost_across_product_ProductGroups_14d"]

In [ ]:
# Group INVOICEITEMS view across different ProductGroups.
invoiceitems_view_by_overall_across_productgroup =\
invoiceitems_view.groupby(
    [], category="ProductGroup"
)

In [ ]:
# Distribution representing the cumulative TotalCost of item, categorized by their respective
# product's ProductGroup, over time.
feature_group =\
invoiceitems_view_by_overall_across_productgroup.aggregate_over(
    "TotalCost", method=fb.AggFunc.SUM,
    feature_names=[
        "OVERALL_item_TotalCost_across_product_ProductGroups"
        + "_" + w for w in windows
    ],
    windows=windows
)
# Get OVERALL_item_TotalCost_across_product_ProductGroups_14d object from feature group.
overall_item_totalcost_across_product_productgroups_14d =\
feature_group["OVERALL_item_TotalCost_across_product_ProductGroups_14d"]

### Compare lookup with aggregation across categories
 See [list of feature transforms](https://docs.featurebyte.com/latest/about/glossary/#feature-transforms)

In [ ]:
# Get the Percentage of a customer's total item TotalCost, that match the ProductGroup of a
# specific product over a 14d period.
customer_x_product_product_productgroup_share_to_customer_item_totalcost_14d =\
customer_item_totalcost_across_product_productgroups_14d.cd.get_relative_frequency(
    product_productgroup
)
customer_x_product_product_productgroup_share_to_customer_item_totalcost_14d.fillna(0)
# Give a name to new feature
customer_x_product_product_productgroup_share_to_customer_item_totalcost_14d.name = \
"CUSTOMER_X_PRODUCT_product_ProductGroup_Share_to_CUSTOMER_item_TotalCost_14d"

In [ ]:
# Get the Percentage of the total item TotalCost, that match the ProductGroup of a specific product
# over a 14d period.
product_productgroup_share_to_overall_item_totalcost_14d =\
overall_item_totalcost_across_product_productgroups_14d.cd.get_relative_frequency(
    product_productgroup
)
product_productgroup_share_to_overall_item_totalcost_14d.fillna(0)
# Give a name to new feature
product_productgroup_share_to_overall_item_totalcost_14d.name = \
"PRODUCT_ProductGroup_Share_to_OVERALL_item_TotalCost_14d"

### Get Representation of Entity attributes
 See [list of feature transforms](https://docs.featurebyte.com/latest/about/glossary/#feature-transforms)

In [ ]:
# Get the representation of a given product_ProductGroup in a given CUSTOMER's item TotalCost
customer_x_product_product_productgroup_representation_in_customer_item_totalcost_14d = (
    customer_x_product_product_productgroup_share_to_customer_item_totalcost_14d
    / product_productgroup_share_to_overall_item_totalcost_14d
)
# Give a name to new feature
customer_x_product_product_productgroup_representation_in_customer_item_totalcost_14d.name = \
"CUSTOMER_X_PRODUCT_product_ProductGroup_Representation_in_CUSTOMER_item_TotalCost_14d"

### Preview feature
 Read on [the feature primary entity concept](https://docs.featurebyte.com/latest/about/glossary/#feature-primary-entity)

 Read on [the serving entity concept](https://docs.featurebyte.com/latest/about/glossary/#serving-entity)

 See [SDK reference for observation table](https://docs.featurebyte.com/latest/reference/core/observation_table/)

 See [SDK reference to preview feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.preview/)

In [ ]:
#Check the primary entity of the feature'
customer_x_product_product_productgroup_representation_in_customer_item_totalcost_14d.primary_entity

In [ ]:
#Get observation table: 'Preview Table with 10 items'
preview_table = catalog.get_observation_table(
	"Preview Table with 10 items"
)

In [ ]:
#Preview CUSTOMER_X_PRODUCT_product_ProductGroup_Representation_in_CUSTOMER_item_TotalCost_14d
customer_x_product_product_productgroup_representation_in_customer_item_totalcost_14d.preview(
	preview_table
)

### Save feature
 See [SDK reference to save feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.save/)

In [ ]:
# Save feature
customer_x_product_product_productgroup_representation_in_customer_item_totalcost_14d.save()

### Add description and see feature definition file
 See [SDK reference for the definition file of a feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.definition/)

In [ ]:
# Add description
customer_x_product_product_productgroup_representation_in_customer_item_totalcost_14d.update_description(
	"The feature assesses the representation of a given "
	"product_ProductGroup in a given CUSTOMER's item TotalCost over a 14d "
	"period. A value greater than 1 indicates this product_ProductGroup is "
	"over-represented for the particular customer. The evaluation is done "
	"by comparing:   - the Percentage of a customer's total item TotalCost,"
	" that match the ProductGroup of a specific product over a 14d period."
	"   - the Percentage of the total item TotalCost, that match the "
	"ProductGroup of a specific product over a 14d period."
)
# See feature definition file
customer_x_product_product_productgroup_representation_in_customer_item_totalcost_14d.definition